In [1]:
from typing import Tuple, Dict
import pandas as pd
import numpy as np
import pickle
from sklearn.manifold import TSNE
import plotly.express as px
import plotly
from sklearn.preprocessing import MinMaxScaler
from scipy.sparse import csr_matrix
import implicit
from implicit.nearest_neighbours import bm25_weight, tfidf_weight
from sklearn.metrics.pairwise import cosine_similarity, euclidean_distances
from scipy.sparse.linalg import svds
from sklearn.decomposition import PCA

In [2]:
import warnings
warnings.filterwarnings("ignore")

# Load data

In [3]:
# Load data from APP DATA folder

with open('../data/features/matrix.pkl', 'rb') as f:
    matrix = pickle.load(f)

with open('../data/features/prof_index_to_prof_name.pkl', 'rb') as f:
    prof_index_to_prof_name = pickle.load(f)

#with open('../data/features/quety_to_prof_index.pkl', 'rb') as f:
#    quety_to_prof_index = pickle.load(f)
    
#with open('data/features/prof_index_to_corrected.pkl', 'rb') as f:
#    prof_index_to_corrected = pickle.load(f)

with open('../data/features/skill_index_to_corrected.pkl', 'rb') as f:
    skill_index_to_corrected = pickle.load(f)
    
with open('../data/features/skill_original_to_index.pkl', 'rb') as f:
    skill_original_to_index = pickle.load(f)
    
skill_df = pd.read_csv('../data/features/skills.csv')
prof_df = pd.read_csv('../data/features/prof.csv')

In [4]:
# see what professions are in database
prof_index_to_prof_name

{0: 'Аналитик данных',
 1: 'Инженер данных',
 2: 'Data Scientist',
 3: 'Продуктовый аналитик',
 4: 'ML инженер',
 5: 'Computer Vision',
 6: 'Администратор баз данных',
 7: 'Аналитик BI',
 8: 'NLP',
 9: 'Аналитик',
 10: 'Big Data',
 11: 'Системный аналитик',
 12: 'Бизнес-аналитик'}

# Create radar plot

In [9]:
# skill x prof matrix
matrix.shape # num_skills x num_profs

(2070, 13)

In [10]:
# filter only top_n_skill_per_profession skill_indexes
# normalize by profession
m_max = np.max(matrix, axis=0)
m_min = np.min(matrix, axis=0)

# min-max scaler
# normalized_matrix = (matrix - m_min) / (m_max - m_min)

# percent of skill occurance: matrix columns sum to 100.0
normalized_matrix = matrix * 100.0 / matrix.sum(axis=0)

In [15]:
# create dataframe from matrix
# prof_index_to_prof_name - dict{idx: profession}
df = pd.DataFrame(normalized_matrix).rename(columns=prof_index_to_prof_name)

# keys from skill dictionary
# skill_index_to_corrected - dict{idx: skill}
# df.index and df['skill_id'] are equal
df['skill_id'] = skill_index_to_corrected.keys() 

# values from skill dictionary
df['Навык'] = skill_index_to_corrected.values()

# check that skill_id match skill name 
assert np.all([skill_index_to_corrected[df['skill_id'][i]] == df['Навык'][i]
               for i in skill_index_to_corrected.keys()])


In [16]:
df.head()

Аналитик данных  Инженер данных  Data Scientist  Продуктовый аналитик  \
0         0.000000        0.000000        0.000000              0.000000   
1         0.835123        0.025233        0.429185              4.961240   
2         0.190885        0.000000        0.099043              0.155039   
3         0.023861        0.782236        0.066028              0.000000   
4         0.000000        0.000000        0.000000              0.000000   

   ML инженер  Computer Vision  Администратор баз данных  Аналитик BI  NLP  \
0    0.000000         0.000000                       0.0     0.000000  0.0   
1    0.090334         0.420168                       0.0     0.000000  0.0   
2    0.090334         0.000000                       0.0     0.487805  0.0   
3    0.361337         0.000000                       0.0     0.000000  0.0   
4    0.000000         0.000000                       0.0     0.000000  0.0   

   Аналитик  Big Data  Системный аналитик  Бизнес-аналитик  skill_id  \
0  0.016869  0.000000            0.000000         0.033025         0   
1  0.421727  0.296150            0.065746         0.231176         1   
2  0.539811  0.394867            6.081525         4.507926         2   
3  0.092780  0.296150            0.000000         0.000000         3   
4  0.008435  0.000000            0.000000         0.000000         4   

               Навык  
0      Навыки продаж  
1          A/B тесты  
2               BPMN  
3   Хранилище данных  
4  Мониторинг метрик

In [19]:
from typing import List
import plotly.graph_objects as go


def plot_polar_graph(df: pd.DataFrame, 
                     prof_list: List[str],
                     intersect_skills: bool = False,
                     top_n: int = 20
                    ) -> plotly.graph_objs.Figure:
    """
    Plot graph in polar coordinates.
    
    Parameters
    ----------
    df: pd.DataFrame
        Skill to Profession matrix (skill in rows, professions in columns)
        with skill id and skill name as additional columns. DataFrame is 
        normalized by profession.
    prof_list: List[str]
        List of profession for what to print the plot.
    intersect_skills: bool
        Whether to intersect popular skills for professions or to union.
        If true, then intersect, otherwise union.
    top_n: int
        Number of top skills per profession. By default = 15.
    
    Returns
    -------
    plotly.graph_objs.Figure
        Figure object for created graph
        
    """
    # create a set of top skills in professions
    skill_set = []
    
    for prof_name in prof_list:
        df_copy = df[[prof_name, 'Навык']].copy()
        # top skills for prof_name
        prof_skill = df_copy.sort_values(by=prof_name, ascending=False)['Навык'][:top_n].values
        
        if intersect_skills: # intersect
            if len(skill_set) == 0:
                skill_set = prof_skill
            skill_set = [x for x in prof_skill if x in skill_set]
        else: # union
            skill_set = skill_set + [x for x in prof_skill if x not in skill_set]

            
    # filter df
    df_copy = df[df['Навык'].isin(skill_set)]
    
    # This block is used for better visualization.
    # We will sort skill_set by skill frequency
    # for the first prof_name in prof_list.
    # You can comment next line to check how it looks without sorting 
    df_copy = df_copy.sort_values(by=prof_list[0], ascending=False)
            
        
    # plot graph
    fig = go.Figure()

    for i, prof_name in enumerate(prof_list):
        # get another radar plot
        fig.add_trace(go.Scatterpolar(
              r=df_copy[prof_name],
              theta=df_copy['Навык'],
              fill='toself',
              name=prof_name
        ))

        # update layout
        fig.update_layout(
          polar=dict(
            radialaxis=dict(
              visible=True
            )),
          showlegend=True
        )
    
    return fig

In [20]:
plot_polar_graph(df, ['NLP', 'Computer Vision'], intersect_skills=True)

In [21]:
plot_polar_graph(df, ['ML инженер', 'Data Scientist'], 
                 intersect_skills=True,
                top_n=25)

In [22]:
plot_polar_graph(df, ['Бизнес-аналитик', 'Системный аналитик'], 
                 intersect_skills=True,
                top_n=25)

In [23]:
plot_polar_graph(df, ['Аналитик данных', 'Аналитик', 'Аналитик BI'], 
                 intersect_skills=True,
                top_n=25)

In [25]:
prof_index_to_prof_name.values()

dict_values(['Аналитик данных', 'Инженер данных', 'Data Scientist', 'Продуктовый аналитик', 'ML инженер', 'Computer Vision', 'Администратор баз данных', 'Аналитик BI', 'NLP', 'Аналитик', 'Big Data', 'Системный аналитик', 'Бизнес-аналитик'])

In [27]:
plot_polar_graph(df, ['Инженер данных', 'Администратор баз данных', 'Big Data'], 
                 intersect_skills=True,
                top_n=25)

In [24]:
# sinonim skills
# ('MS Excel', 'Excel')
# ('Финансовый анализ', 'Анализ финансовых показателей')

# Create scatter plot

В функцию ниже добавлены два новых параметра: 
- norm_type: способ нормализации матрицы навык-профессия
- factor_alg_type: способ преобразования матрицы, полученной после нормализации, для улучшения визуализации

В любом случае последним слоем преобразование будет приведение полученных эмбеддингов навыков к двумерному виду через TSNE, так как этот метод позволяет сохранить пространственную ориентацию между векторами: близкие вектора будут отображены как близкие точки, и наоборот.

 (PCA, UMAP)

In [29]:
import umap
# pip install umap-learn

In [16]:
def prepare_plot_df(skill_df: pd.DataFrame,
                    matrix: np.array,
                    skill_index_to_corrected: Dict[int, str],
                    prof_index_to_corrected: Dict[int, str], 
                    top_n_skill_per_profession: int = 200, 
                    salary: Tuple[float, float] = None,
                    norm_type: str = 'none',
                    factor_alg_type: str = 'none', perplexity: int = 30,
                    early_exaggeration=12,
                    learning_rate=200,
                    dim: int = 5,
                    use_tsne=True
                    ) -> Tuple[pd.DataFrame, pd.DataFrame]:
    """Prepare datafame for plotting
    
        Parameters
        ----------
        skill_df: pd.DataFrame
            Data frame of skills
        matrix: np.array
            Skill to Profession matrix (skill in rows, professions in columns)
        skill_index_to_corrected: Dict[int, str]
            Dictionary from index to skill name
        prof_index_to_corrected: Dict[int, str]
            Dictionary from index to profession name
        top_n_skill_per_profession: int
            maximum skills for each profession
        salary: Tuple[float, float]:
            filter by salary, from and to, or None
            !!! do not set because too low vacancies with salary
        norm_type: str
            How normalize skill-prof matrix ('none', 'skill', 'prof', 'bm', 'tfidf')
        factor_alg_type: str
            Type of algorithm to transform normalized matrix 
            for better visuzlization 
            ('svd', 'als', 'sim_euclid', 'pca', 'sim_cos', 'none')
        dim: int
            Dimensionality of matrix after factorization. Used in PCA and SVD mode of factor_alg_type.

        Returns
        -------
        Tuple[pd.DataFrame, pd.DataFrame] : 
            - DataFrame for skill map plot
            - DataFrame for profession map plot
    
    
    """

    def apply_filter(df, top_n_skill_per_profession, salary):
        if salary is not None:
            df = df[(df.salary_q75 > salary[0]) & (df.salary_q25 <= salary[1])]
        if top_n_skill_per_profession is not None:
            df = df.head(top_n_skill_per_profession)
        return df

    
    skill_filter_indexes = []
    for p in prof_index_to_corrected.values():
        skills_per_profession = skill_df.sort_values(p, ascending=False)
        skills_per_profession = apply_filter(skills_per_profession, top_n_skill_per_profession, salary)

        skill_filter_indexes = skill_filter_indexes + \
            [x for x in skills_per_profession.skill_id if x not in skill_filter_indexes]
#     print(len(skill_filter_indexes))
    
    # Normalization
    m = matrix[skill_filter_indexes, :].T
    
    if norm_type == 'skill':
        # norm for earch skill
        m = m / np.sum(m, axis=0, keepdims=True)
    elif norm_type == 'prof':
        # norm for each prof
        m = m / np.sum(m, axis=1, keepdims=True)
    elif norm_type == 'bm':
        m = np.asarray(bm25_weight(m).todense())
    elif norm_type == 'tfidf':
        m = np.asarray(tfidf_weight(m).todense())
    elif norm_type != 'none':
        raise ValueError("norm_type parametr must be ('none', 'skill', 'prof', 'bm', 'tfidf')")

    # create embeddings
    # als is needed for professions because T-NSE doesn't work with few objects
    csr = csr_matrix(m)
    model = implicit.als.AlternatingLeastSquares(factors=2, regularization=0.0, iterations=20)
    model.fit(csr)
    profs_xy = model.user_factors
#     print(csr.shape)

    if factor_alg_type == 'svd':
        skills_xy, _, _ = svds(csr.T, k=dim)
    elif factor_alg_type == 'pca':
        pca = PCA(n_components=dim)
        skills_xy = pca.fit_transform(m.T)
    elif factor_alg_type == 'als':
        skills_xy = model.item_factors
    elif factor_alg_type == 'sim_euclid':
        skills_xy = euclidean_distances(m.T)
    elif factor_alg_type == 'sim_cos':     
        skills_xy = cosine_similarity(m.T)
    elif factor_alg_type == 'umap':
#         skills_xy = cosine_similarity(m.T)
        skills_xy = umap.UMAP(n_neighbors=10).fit_transform(m.T)
    elif factor_alg_type == 'none':
        skills_xy = m.T.copy()
    else:
        raise ValueError("skills_xy parametr must be ('svd', 'pca', als', 'none')")
    
    if use_tsne:
        skills_xy = TSNE(n_components=2, perplexity=perplexity, 
                         early_exaggeration=early_exaggeration,
                        learning_rate=learning_rate).fit_transform(skills_xy)
#     print(skills_xy.shape)
    df = pd.DataFrame(skills_xy).rename(columns={0:'x',1:'y'})
    df['skill_id'] = list(skill_filter_indexes)
    df['Навык'] = df.skill_id.apply(lambda x: skill_index_to_corrected[x])

    # be ensure that for every profession has skill point 
    # (one skill may be in severall professions)
    df_plot_skill = None
    for p in prof_index_to_corrected.values():

        skills_per_profession = skill_df.sort_values(p, ascending=False)
        skills_per_profession = apply_filter(skills_per_profession, top_n_skill_per_profession, salary)
        ids = skills_per_profession.skill_id.to_numpy()

        df_for_prof = df[df.skill_id.isin(ids)]
        df_for_prof['Профессия'] = p

        min_f = skills_per_profession[p].min()
        max_f = skills_per_profession[p].max()
        if max_f - min_f < 1e-10:
            max_f += 1
        size_series = skills_per_profession[p].apply(lambda x: (x - min_f) / (max_f - min_f))
        size_dict = pd.Series(size_series.values, index=skills_per_profession.skill_id).to_dict()
        df_for_prof['size'] = df_for_prof.skill_id.apply(lambda x: 15 * size_dict[x] + 0.8)
#         df_for_prof['size'] = df_for_prof.skill_id.apply(lambda x: size_dict[x])

        if df_plot_skill is None:
            df_plot_skill = df_for_prof
        else:
            df_plot_skill = pd.concat([df_plot_skill, df_for_prof])

    df_plot_prof = pd.DataFrame(profs_xy).rename(columns={0:'x',1:'y'})
    df_plot_prof['Профессия'] = pd.Series(df_plot_prof.index).apply(lambda x: prof_index_to_corrected[x])

    return df_plot_skill, df_plot_prof
#     return df, df_plot_prof

In [17]:
def plot_skill_map(df: pd.DataFrame, width=1000, height=600) -> plotly.graph_objs.Figure:
    
    # custom colormap
    color_list = [
        '#AA0DFE', '#3283FE', '#1CBE4F', '#C4451C',
        '#FE00FA', '#325A9B', '#FEAF16', '#F8A19F',
        '#90AD1C', '#F6222E', '#2ED9FF', '#B10DA1',
        '#C075A6', '#FC1CBF', '#B00068', '#FBE426',
        '#FA0087'
    ]
    
    # custom visualization order
    # for better reproducability
    prof_order = ['NLP', 'Big Data', 'Инженер данных', 'Бизнес-аналитик',
     'ML инженер', 'Администратор баз данных', 'Продуктовый аналитик',
    'Data Scientist', 'Аналитик данных', 'Computer Vision', 'Аналитик BI',
    'Системный аналитик', 'Аналитик']
    
    fig = px.scatter(df, x='x', y='y',
                    color='Профессия', hover_name='Навык', 
                    hover_data= {'x':False, 'y':False, 'size':False, 'Профессия': False},
                    size='size', category_orders={'Профессия': prof_order},
#                     color_discrete_sequence=px.colors.qualitative.Alphabet, 
                    color_discrete_sequence=color_list,
                     title = None, width=width, height=height)

    fig.update_traces(marker=dict(opacity=0.75, line=dict(width=0.5, color='DarkSlateGrey')), 
                  selector=dict(mode='markers'))

#     fig.update_xaxes(visible=False)
#     fig.update_yaxes(visible=False)

    return fig

Есть навыки, которые очень часто требуются в сфере ИТ. К ним относится знание языков программирования, английский, какие-то софт-скилы. И есть наоборот очень специфичные навыки, которые не часто указываются при публикации вакансии.  

Можно провести аналогию со сферой обработки естественного языка. Там слова, которые часто встречаются вне зависимости от темы, обычно считают неинформативными (служебные слова, междометия, предлоги, союзы и т.п.) и назначают им маленьшие веса (tf-idf), либо же вообще выбрасывают из словаря. Но нам такая идея не подходит, потому что часто встречаемые навыки несут в себе информацию о профессии, в отличии от служебных слов в документе. То есть вариант с нормализацией по tf-idf можно не рассматривать. (norm_type='tfidf')   

Нормировка таблицы по скилам позволит лишь привести векторы к одному масштабу, но отрицательно скажется на понимании роли того или иного навыка внутри конкретной профессии. Так происходит потому, что в этом случае соотношения между значениями признаков для различных навыков будут потеряны. А нас интересует как раз связь между различными навыками. (norm_type='skill')

Логично рассматривать навыки по частоте встречаемости внутри профессии (нормировка по профессии). Таким образом мы получим "распределение" частоты встречаемости навыков по профессиям. (norm_type='prof')

Еще один вариант - использовать для нормализации матрицы алгоритм bm25. (norm_type='bm')

После нормализации матрицы нам необходимо применить алгоритм понижения размерности. Остановимся на алгоритме T-SNE, так как он показал наилучшие результаты на наших данных. Этот алгоритм позволяет отображать близкие в некотором смысле вектора в близкие точки на плоскости и наоборот.    

P.S. Ниже представлены эксперименты с другими алгоритмами: PCA и UMAP.

Перед тем, как уменьшать размерность, можно попробовать преобразовать строки матрицы к какому-то виду, который позмолит наилучшим образом отобразить точки. (Преобразование определяется параметром factor_alg_type)

Можно рассмотреть и исходные вектора (без преобразований). В этом случае большие по норме вектора будут ближе к большим, а меньшие - к меньшим. Большие по норме вектора - это те навыки, которые часто встречаются среди всех профессий (например, Python). Такие вектора на многих позициях имеют большие значения, и на графике будут изображаться жирной точкой. Маленькие - наоборот. 

**Нормировка: по профессии, дополнительное преобразование: нет.**

В принципе, кое-какие классы выделяются, выглядит даже более менее логично.

In [18]:
df_plot_skill, df_plot_prof = prepare_plot_df(skill_df, matrix, skill_index_to_corrected,
                                              prof_index_to_prof_name, 
                                              top_n_skill_per_profession=30,
                                              norm_type='prof', factor_alg_type='none', dim=2,
                                              use_tsne=True, perplexity=30
                                             )

plot_skill_map(df_plot_skill.sort_values(by='size', ascending=False)).show()

  0%|          | 0/20 [00:00<?, ?it/s]

In [26]:
df_plot_skill, df_plot_prof = prepare_plot_df(skill_df, matrix, skill_index_to_corrected,
                                              prof_index_to_prof_name, 
                                              top_n_skill_per_profession=20,
                                              norm_type='prof', factor_alg_type='none', dim=2,
                                              use_tsne=True, perplexity=10
                                             )

plot_skill_map(df_plot_skill.sort_values(by='size', ascending=False)).show()

  0%|          | 0/20 [00:00<?, ?it/s]

**Нормировка: по профессии, дополнительное преобразование: попарное косинусное расстояние**   

Посчитаем попарное косинусное расстояние между векторами навыков и будем использовать полученные значения в качестве новых признаков.

В случае, когда все множество точек, соответствующих навыкам, представляет собой некое облако точек, разбитое на отдельные сектора (углы) в соответствии с профессиями, косинусное расстояние поможет сделать для каждой профессии свой шарообразный кластер. (Можно сравнить визуализации сверху и снизу и понять, о чем речь)

Таким образом мы уберем единый шар, разбитый на сектора. Векторы, которые попали в один сектор шара, будут схлопнуты в отдельные множества. Мы получим несколько шарообразных кластеров, каждый из которых содержит точки, соответствующие навыкам для отдельной профессии. Понятно, что в реальности такое встретить вряд ли удастся, но идея ясна.


In [20]:
df_plot_skill, df_plot_prof = prepare_plot_df(skill_df, matrix, skill_index_to_corrected,
                                              prof_index_to_prof_name, 
                                              top_n_skill_per_profession=20, perplexity=20,
                                              norm_type='prof', factor_alg_type='sim_cos', dim=5)
plot_skill_map(df_plot_skill).show()
# plot_skill_map(df_plot_skill.sort_values(by='size', ascending=False)).show()

  0%|          | 0/20 [00:00<?, ?it/s]

**Нормировка: по профессии, дополнительное преобразование: попарное евклидово расстояние**    

Посчитаем попарное Евклидово расстояние между векторами навыков и будем использовать полученные значения в качестве нового признакового описания навыков.


Если навыки часто встречаются среди всех профессий, то при нормировке по профессиям эти навыки будут иметь вектора, большие по норме (точнее сказать с большими значениями по каждой координате). По метрике Евклида вектора с большой нормами будут  в любом случае ближе друг к другу, чем к векторам с маленькой нормой. 

Поэтому на графике наблюдается скопление "больших" точек в одном месте и рассеяние более мелких точек по остальному пространству.   
Кластеры явным образом не выделяются. Визуализация может показаться интересной с определенной точки зрения. Если полностью очистить график и начинать добавлять по одному классу, можно заметить, что основные навыки (которые требуются практически везде, изображены жирными точками в соответствии с частотой встречаемости внутри профессии) концентрируются в определенной области, на некоторой кривой за ними расположены навыки средней востребованности и далее редко упоминающиеся навыки. При добавлении следующего класса можно увидеть, что он имеет общее начало с кривой для предыдущего класса (область жирных точек), и затем новая кривая начинает отклоняться в какую-то сторону (одбласть мелких точек). И так далее.  

Расположение кривых различных классов относительно друг друга может быть различным. Некоторые кривые встраиваются между кривыми других классов (Продуктовый аналитик между Аналитиком данных и Аналитиком BI), некоторые - почти полностью повторяют другую кривую с небольшими отклонениями (Аналитик и Аналитик BI, NLP и Computer Vision), некоторые - сильно отличаются от остальных (Администратор баз данных).

In [21]:
df_plot_skill, df_plot_prof = prepare_plot_df(skill_df, matrix, skill_index_to_corrected,
                                              prof_index_to_prof_name, 
                                              top_n_skill_per_profession=30, perplexity=30,
                                              norm_type='prof', factor_alg_type='sim_euclid', dim=5)
#                                               norm_type='prof', factor_alg_type='pca', dim=5)


plot_skill_map(df_plot_skill).show()

  0%|          | 0/20 [00:00<?, ?it/s]

### Остальные комбинации алгоритмов

Некоторые наблюдения:
- SVD и PCA выглядят очень похоже. На самом деле и с точки зрения теории это близкие преобразования.


In [22]:
for norm_type in ['none', 'skill', 'prof', 'bm']:
    for factor_alg_type in ['svd', 'pca', 'sim_cos', 'none']:

        df_plot_skill, df_plot_prof = prepare_plot_df(
            skill_df, matrix, 
            skill_index_to_corrected, 
            prof_index_to_prof_name, 
            top_n_skill_per_profession=30, 
            norm_type=norm_type, perplexity=10,
            factor_alg_type=factor_alg_type
        )

        print(f'Norm: {norm_type}\tFactor: {factor_alg_type}')
        plot_skill_map(df_plot_skill).show()
        #plot_prof_map(df_plot_prof).show()

        #df_plot_skill.to_csv(f'data/plot_df/{a}-{n}-{top}-skill.csv')
        #df_plot_prof.to_csv(f'data/plot_df/{a}-{n}-{top}-prof.csv')


  0%|          | 0/20 [00:00<?, ?it/s]

Norm: none	Factor: svd


  0%|          | 0/20 [00:00<?, ?it/s]

Norm: none	Factor: pca


  0%|          | 0/20 [00:00<?, ?it/s]

...

Norm: bm	Factor: pca


  0%|          | 0/20 [00:00<?, ?it/s]

Norm: bm	Factor: sim_cos


  0%|          | 0/20 [00:00<?, ?it/s]

Norm: bm	Factor: none


### Понижение размерности с помощью PCA и SVD

Здесь мы используем параметр ```use_tsne=False```, чтобы отключить T-SNE преобразование. При этом для понижения размерности используем ```factor_alg_type=['pca', 'svd']``` и указываем ```dim=2```.

In [23]:
for norm_type in ['none', 'prof', 'skill', 'bm']:
    for factor_alg_type in ['pca', 'svd']:
        print(norm_type, factor_alg_type)
        df_plot_skill, df_plot_prof = prepare_plot_df(skill_df, matrix, skill_index_to_corrected,
                                                      prof_index_to_prof_name, 
                                                      top_n_skill_per_profession=50,
                                                      norm_type=norm_type, factor_alg_type=factor_alg_type, dim=2, 
                                                      use_tsne=False)

        plot_skill_map(df_plot_skill.sort_values(by='size', ascending=False)).show()

none pca


  0%|          | 0/20 [00:00<?, ?it/s]

none svd


  0%|          | 0/20 [00:00<?, ?it/s]

prof pca


...

  0%|          | 0/20 [00:00<?, ?it/s]

bm pca


  0%|          | 0/20 [00:00<?, ?it/s]

bm svd


  0%|          | 0/20 [00:00<?, ?it/s]

### Понижение размерности с помощью UMAP

In [24]:
# df_plot_skill, df_plot_prof = prepare_plot_df(skill_df, matrix, skill_index_to_corrected,
#                                               prof_index_to_prof_name, 
#                                               top_n_skill_per_profession=50,
#                                               norm_type='prof', factor_alg_type='umap', dim=2,
#                                               use_tsne=False
#                                              )

# plot_skill_map(df_plot_skill.sort_values(by='size', ascending=False)).show()

In [25]:
# df_plot_skill, df_plot_prof = prepare_plot_df(skill_df, matrix, skill_index_to_corrected,
#                                               prof_index_to_prof_name, 
#                                               top_n_skill_per_profession=50,
#                                               norm_type='bm', factor_alg_type='umap', dim=2,
#                                               use_tsne=False
#                                              )

# plot_skill_map(df_plot_skill.sort_values(by='size', ascending=False)).show()